In [1]:
import pandas as pd
from sklearn.cluster import KMeans
from sklearn.impute import SimpleImputer
from scipy.spatial.distance import euclidean
import folium

# Loading the dataset
dataset = pd.read_csv(r"C:\Users\vignesh\Desktop\sem1\math\Project_3\input.csv")

# Checking for NaN values
print("Before handling missing values:")
print(dataset.isnull().sum())

# Handling missing values using SimpleImputer
imputer = SimpleImputer(strategy='mean')
dataset[['latitude', 'longitude']] = imputer.fit_transform(dataset[['latitude', 'longitude']])

# Check again after handling missing values
print("After handling missing values:")
print(dataset.isnull().sum())

# Extracting features for clustering (e.g., latitude and longitude)
features = dataset[['latitude', 'longitude']]

# Define the number of clusters (k)
num_clusters = 3

# Initialize the KMeans model
kmeans_model = KMeans(n_clusters=num_clusters, random_state=0)

# Fit the model to the data
kmeans_model.fit(features)

# Obtain cluster labels for each data point
cluster_labels = kmeans_model.labels_

# Add cluster labels to the dataset
dataset['cluster'] = cluster_labels

# Calculate the number of incidents in each cluster
cluster_counts = dataset['cluster'].value_counts()

# Get the coordinates of the centroids
centroids = kmeans_model.cluster_centers_
print("Cluster centroids coordinates:")
for i, centroid in enumerate(centroids):
    print(f"Centroid {i}: {centroid}")

# Calculate distances between centroids
distances = {}
for i in range(num_clusters):
    for j in range(i + 1, num_clusters):
        dist = euclidean(centroids[i], centroids[j])
        distances[f"Distance between centroid {i} and centroid {j}"] = dist

print("Distances between centroids:")
for key, value in distances.items():
    print(f"{key}: {value}")

# Creating a map centered around the mean latitude and longitude
map_center = [dataset['latitude'].mean(), dataset['longitude'].mean()]
map_clusters = folium.Map(location=map_center, zoom_start=5)

# Define colors for clusters
colors = ['black', 'red', 'green']

# Add data points to the map with cluster colors
for index, row in dataset.iterrows():
    folium.CircleMarker(
        location=[row['latitude'], row['longitude']],
        radius=5,
        color=colors[row['cluster']],
        fill=True,
        fill_color=colors[row['cluster']],
        fill_opacity=0.7,
        popup=f"Cluster: {row['cluster']}<br>Incidents: {cluster_counts[row['cluster']]}",
    ).add_to(map_clusters)

# Add centroids to the map
for i, centroid in enumerate(centroids):
    folium.Marker(
        location=centroid,
        icon=folium.Icon(color=colors[i], icon="star"),
        popup=f"Centroid {i}: {centroid}"
    ).add_to(map_clusters)

# Save the map as an HTML file
map_clusters.save("cluster_map2.html")

# Display the map
map_clusters


Before handling missing values:
id                           0
name                       262
date                         0
manner_of_death              0
armed                      203
age                        304
gender                       3
race                       711
city                         0
state                        0
signs_of_mental_illness      0
threat_level                 0
flee                       472
body_camera                  0
latitude                   303
longitude                  303
is_geocoding_exact           0
dtype: int64
After handling missing values:
id                           0
name                       262
date                         0
manner_of_death              0
armed                      203
age                        304
gender                       3
race                       711
city                         0
state                        0
signs_of_mental_illness      0
threat_level                 0
flee                     